In [ ]:
import re
import json
import pickle
from pathlib import Path
from collections import OrderedDict, defaultdict
from tqdm import tqdm
from utils_sel import *
from bs4 import BeautifulSoup, NavigableString, Tag, Comment
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import NoSuchElementException

## Local functions

In [ ]:
HOME_URL = "https://web.meis.ee/testest/goto.php?target=root_1&client_id=integratsioon"
SAVE_PATH = Path('./estonian_language_exams/')

def initialize(production=True):
  driver = get_driver(production)
  driver.get(HOME_URL)
  close_popup = driver.find_element(By.ID, value='sb-nav-close')
  WebDriverWait(driver, 10).until(EC.element_to_be_clickable(close_popup))
  close_popup.click()
  return driver

def get_tests(driver):
  tests = driver.find_element(By.CLASS_NAME, 'ilContainerItemsContainer').find_elements(By.TAG_NAME, 'h4')
  tests = [elem.find_element(By.TAG_NAME, 'a') for elem in tests]
  links = [elem.get_attribute('href') for elem in tests]
  names = [elem.text for elem in tests]
  return links, names

def start_test(driver):
  click_button(driver, 'cmd[startPlayer]')
  click_button(driver, 'cmd[accessCodeConfirmed]')

def finish_test(driver):
  click_link(driver, 'Lõpeta test')
  click_link(driver, 'Vaata vastuseid')

def get_test_table(driver):
  table = driver.find_element(By.CLASS_NAME, 'table-striped').find_element(By.TAG_NAME, 'tbody')
  questions = table.find_elements(By.TAG_NAME, 'a')
  links = [elem.get_attribute('href') for elem in questions]
  names = [elem.text for elem in questions]
  ids = [int(elem.find_elements(By.TAG_NAME, 'td')[1].text) for elem in table.find_elements(By.TAG_NAME, 'tr')]
  return links, names, ids

def get_answers_single_type(driver):
  instruction = driver.find_element(By.CLASS_NAME, 'ilc_heading3_Headline3').text
  questions_answers = driver.find_elements(By.CLASS_NAME, 'ilc_question_SingleChoice')
  question = questions_answers[0].find_element(By.CLASS_NAME, 'ilc_qtitle_Title').text
  answers = questions_answers[1].find_elements(By.CLASS_NAME, 'ilc_qanswer_Answer')
  options = [elem.text.strip() for elem in answers]
  correct = [i+1 for i, elem in enumerate(answers) if elem.find_element(By.TAG_NAME, 'img').get_attribute('alt')=='Kontrollitud']
  assert len((instruction + question).strip()) > 0
  assert len(correct) == 1
  return instruction, question, options, str(correct[0])

def get_page_title_html(driver):
  page = driver.find_element(By.ID, 'ilc_Page')
  page_html = get_html_with_images(driver, page)
  page_name = page.find_element(By.CLASS_NAME, 'ilc_page_title_PageTitle').text.strip()
  return page_name, page_html

def toggle_top_bar(driver, visible=False):
    script = f"""
    var topBars = document.getElementsByClassName('ilTopFixed');
    for (var i = 0; i < topBars.length; i++) {{
        topBars[i].style.display = '{'' if visible else 'none'}';
        topBars[i].style.visibility = '{'' if visible else 'hidden'}';
    }}
    """
    driver.execute_script(script)

def hide_own_answer(driver):
  questions = driver.find_elements(By.CLASS_NAME, 'ilc_question_Standard')
  instruction = driver.find_element(By.CLASS_NAME, 'ilc_qtitle_Title')
  copy_element_as_first_child(driver, instruction, questions[1].find_element(By.XPATH, "./div"))
  hide_between_start_end(driver, questions[0].get_property('parentNode'), 'Sinu vastus oli:', 'Õige vastus on:')

def get_page_screenshot(driver, remove_own=True, as_bytes=True):
  toggle_top_bar(driver)
  div = driver.find_element(By.ID, 'ilc_Page')
  if remove_own:
    hide_own_answer(driver)
  im = take_full_div_screenshot(driver, div)
  if as_bytes:
    return image_to_bytes(im)
  return im

def get_first_num_from_title(title):
  match = re.search(r'\s(\d+)\.\s', title)
  return int(match.group(1))

def save_all_questions(driver, save_dict):
  continue_questions = True
  while continue_questions:
    title, html = get_page_title_html(driver)
    save_dict[title] = {'html_question': html}
    try:
      click_link(driver, 'Järgmine')
    except NoSuchElementException:
      continue_questions = False

def nums_from_title(title):
    matches = re.findall(r'(\d+)\.', title)
    nums = [int(match) for match in matches][1:]
    if len(nums) == 2:
      nums = list(range(nums[0], nums[1]+1))
    return nums

def extract_number_and_text(string):
    match = re.match(r'^(\d+)\.\s(.+)$', string)
    if match:
        return int(match.group(1)), match.group(2)
    else:
        return None

def extract_letter_and_text(string):
    match = re.match(r'^([A-Z]+)\s+(.+)$', string)
    if match:
        return match.group(1), match.group(2)
    else:
        return None

def has_repeated(any_list):
  return len(any_list) != len(set(any_list))

def sep_num_ABC_mult(text):
  quests = []
  opts_dic = defaultdict(list)
  for elem in text.split('\n'):
    if txt := elem.strip():
      if num_txt := extract_number_and_text(txt):
        quests.append(num_txt)
      elif alf_txt := extract_letter_and_text(txt):
        opts_dic[quests[-1][0]].append(alf_txt)
  assert all(len(o) > 1 for o in opts_dic.values())
  opts_list = [opts_dic[q[0]] for q in quests]
  return quests, [[s[0] for s in ops] for ops in opts_list], [[s[1] for s in ops] for ops in opts_list]

## The simple and nicely formated MQA questions

In [ ]:
sd_pkl_path = SAVE_PATH / 'simple_data.pkl'
if sd_pkl_path.exists():
  with sd_pkl_path.open('rb') as file:
    simple_data = pickle.load(file)
else:
  simple_data = OrderedDict()
  driver = initialize()
  click_link(driver, 'Sõeltestid')
  tests_links, tests_names = get_tests(driver)
  for test_link, test_name in zip(tests_links, tests_names):
    simple_data[test_name] = OrderedDict()
    driver.get(test_link)
    start_test(driver)
    finish_test(driver)
    links, names, ids = get_test_table(driver)
    for url, title, id in zip(links, tqdm(names), ids):
      driver.get(url)
      instruction, question, options, correct = get_answers_single_type(driver)
      simple_data[test_name][id] = {
        "category_original_lang": test_name,
        "original_question_num": get_first_num_from_title(title),
        "question": instruction + '\n' + question,
        "options": options,
        "answer": correct,
        "html": get_page_title_html(driver)[1],
        "image": get_page_screenshot(driver)
      }
  driver.close()
  with sd_pkl_path.open('wb') as file:
    pickle.dump(simple_data, file)
  image_list = []
  for test_name in simple_data.keys():
    image_list.append(create_image_from_text(test_name))
    for id in simple_data[test_name].keys():
      image_list.append(simple_data[test_name][id]['image'])
  create_pdf_from_images(image_list, SAVE_PATH / 'Sõeltestid.pdf')

## Questions that have varying formatting

### Saving the pages

In [ ]:
cx_pkl_path = SAVE_PATH / 'complex_data.pkl'
if cx_pkl_path.exists():
  with cx_pkl_path.open('rb') as file:
    complex_data = pickle.load(file)
else:
  complex_data = OrderedDict()
  driver = initialize()
  for complex in ['Diagnoostestid', 'Tasemeeksami näidistestid']:
    complex_data[complex] = OrderedDict()
    click_link(driver, complex)
    tests_links, tests_names = get_tests(driver)
    for test_link, test_name in zip(tests_links, tests_names):
      driver.get(test_link)
      tests_links2, tests_names2 = find_links_names(driver, 'lugemistest')
      for test_link2, test_name2 in zip(tests_links2, tests_names2):
        complex_data[complex][test_name2] = OrderedDict()
        driver.get(test_link2)
        start_test(driver)
        save_all_questions(driver, complex_data[complex][test_name2])
        finish_test(driver)
        links, names, ids = get_test_table(driver)
        for url, title, id in zip(links, tqdm(names, desc=test_name2), ids):
          driver.get(url)
          complex_data[complex][test_name2][title]['html'] = get_page_title_html(driver)[1]
          complex_data[complex][test_name2][title]['image'] = get_page_screenshot(driver)
    driver.get(HOME_URL)
  driver.close()
  with cx_pkl_path.open('wb') as file:
    pickle.dump(complex_data, file)
  image_list = []
  for complex in complex_data.keys():
    image_list.append(create_image_from_text(complex))
    for test_name2 in complex_data[complex].keys():
      image_list.append(create_image_from_text(test_name2))
      for title in complex_data[complex][test_name2].keys():
        image_list.append(complex_data[complex][test_name2][title]['image'])
  create_pdf_from_images(image_list, SAVE_PATH / 'complex_data.pdf')

### Extracting the complex data

In [ ]:
driver = get_driver()
body = driver.find_element(By.TAG_NAME, 'body')

#### Helper funcs for Soup

In [ ]:
def get_text(tag: Tag) -> str:
  driver.execute_script('document.body.innerHTML=arguments[0]', str(tag))
  return body.text

def get_elements_between(start_element, end_element):
    elements_between = []
    current = start_element.next_sibling
    while current and current != end_element:
        if current.name:  # Check if it's a tag and not just text
            elements_between.append(current)
        current = current.next_sibling
    return elements_between

def smart_get_text(element):
    if isinstance(element, Tag) and element.name == 'table':
        return process_table(element)
    text = get_text(element)
    tables = element.find_all('table')
    for table in tables:
        table_text = process_table(table)
        text = text.replace(get_text(table), table_text)
    return re.sub(r'\s*\n\s*', '\n', text).strip()

def process_table(table):
    rows = table.find_all('tr')
    if len(rows) == 2:
        data = defaultdict(list)
        headers = []
        for i, row in enumerate(rows):
            cells = row.find_all(['th', 'td'])
            for j, cell in enumerate(cells):
                cell_text = get_text(cell).replace('\n', '  ')
                if i == 0:
                    headers.append(cell_text)
                    data[cell_text] = []  # Initialize the list for this header
                if i > 0 or len(rows) == 1:  # Add data for single-row tables too
                    data[headers[j]].append(cell_text)
        table_strings = []
        for header, values in data.items():
            table_strings.append(f"{header}:\n{', '.join(values)}")
        return '\n'.join(table_strings)
    else:
        return get_text(table)

def get_base_question(soup):
  instruction = soup.find('h3').getText(strip=True)
  question_div = soup.find('div', {'class': 'ilc_question_Standard'})
  middle_elems = get_elements_between(soup.find('h3'), question_div)
  middle_context = '\n\n'.join([smart_get_text(elem) for elem in middle_elems]) + '\n\n'
  question = soup.find('div', {'class': 'ilc_qtitle_Title'}).getText(strip=True)
  return f'{instruction}\n\n{middle_context}{question}'

def get_opt_an_simple(mqas, soup_answer):
  options = [get_text(mqa.parent.parent).strip() for mqa in mqas]
  correct_div = soup_answer.find_all('div', {'class': 'ilc_question_SingleChoice'})[1]
  imgs = correct_div.find_all('img')
  answer = [i+1 for i, img in enumerate(imgs) if img.attrs['title']=="Kontrollitud"]
  assert len(answer) == 1
  answer = int(answer[0])
  return options, answer

def get_opt_an_sel1(select_elem, soup_answer):
  options = [elem.getText(strip=True) for elem in select_elem(['option']) if int(elem.attrs['value'])>=0]
  correct_div = soup_answer.find_all('div', {'class': 'ilc_question_Standard'})[1]
  answer = 1 + options.index(correct_div.find('span', {'class': 'solutionbox'}).getText(strip=True))
  assert answer > 0
  return options, answer

def get_opt_an_sel_many(soup, soupan):
  question_div = soup.find('div', {'class': 'ilc_question_Standard'})
  select_elems = question_div.find_all('select')
  if len(soup(['img'])) > 0 or len(question_div(['strong'])) > 0:
    return [], [], [] # discard questions with images or mult completions
  parents = [elem.parent for elem in select_elems]
  select_elems = [elem.extract() for elem in select_elems]
  nums_subques = [extract_number_and_text(s.getText(strip=True)) for s in parents]
  if any(x is None for x in nums_subques):
    return [], [], [] # discard unexpected formats
  ans_div = soupan.find_all('div', {'class': 'ilc_question_Standard'})[1]
  ans_txt = [ele.getText(strip=True) for ele in ans_div.find_all('span', {'class': 'solutionbox'})]
  opts = [[elem.getText(strip=True) for elem in elems(['option']) if int(elem.attrs['value'])>=0] for elems in select_elems]
  anss = [1+ops.index(ans) for ans, ops in zip(ans_txt, opts, strict=True)]
  assert any(a>0 for a in anss)
  if has_repeated(nums_subques):
    nums_subques, opts2, opts_expl = sep_num_ABC_mult(parents[0].getText('\n', strip=True))
    assert opts == opts2
    return opts_expl, anss, [s[1] for s in nums_subques]
  return opts, anss, [s[1] for s in nums_subques]

def get_complex(ans_html, que_html):
  soup = BeautifulSoup(que_html, 'html.parser')
  soupan = BeautifulSoup(ans_html, 'html.parser')
  question = get_base_question(soup)
  select_elems = soup(['select'])
  mqas = soup.find_all('input', {'name': 'multiple_choice_result'})
  if len(mqas) > 1:
    options, answer = get_opt_an_simple(mqas, soupan)
    return [question], [options], [answer]
  elif len(select_elems) == 1:
    options, answer = get_opt_an_sel1(select_elems[0], soupan)
    return [question], [options], [answer]
  elif len(select_elems) > 1:
    optionss, answers, sub_questions = get_opt_an_sel_many(soup, soupan)
    if len(answers) > 0:
      return [f'{question}\n\n{sub}' for sub in sub_questions], optionss, answers
  return [], [], []

#### Running

In [ ]:
data_list = []
img_list_ok = []
for complex in complex_data.keys():
  img_list_ok.append(create_image_from_text(complex))
  for test_name2 in complex_data[complex].keys():
    img_list_ok.append(create_image_from_text(test_name2))
    for title in complex_data[complex][test_name2].keys():
      data = complex_data[complex][test_name2][title]
      data['category_original_lang'] = test_name2 + ' ' + title
      nums = nums_from_title(title)
      ques, opts, anss = get_complex(data['html'], data['html_question'])
      if len(anss) == 0 or any(len(o) == 1 for op in opts for o in op):
        continue
      assert len(anss) == len(nums)
      img_list_ok.append(data['image'])
      for num, que, opt, ans in zip(nums, ques, opts, anss, strict=True):
        data_new = data.copy()
        data_new['original_question_num'] = num
        data_new['question'] = que
        data_new['options'] = opt
        data_new['answer'] = ans
        data_list.append(data_new)
create_pdf_from_images(img_list_ok, SAVE_PATH / 'Diagnoostestid.pdf')

## Saving the Final JSON

In [ ]:
final_list = []
questions = set()
base_model = {
  "language": "et",
  "country": "Estonia",
  "source": "https://web.meis.ee/testest/goto.php?target=root_1&client_id=integratsioon",
  "license": "open",
  "level": "Elementary",
  "category_en": "Language Proficiency Test",
  "category_original_lang": "Eesti keele tasemeeksamid"
}

In [ ]:
base_model['file_name'] = 'Sõeltestid.pdf'
for test_name in simple_data.keys():
  for id in simple_data[test_name].keys():
    base = base_model.copy()
    data = simple_data[test_name][id]
    base["original_question_num"] = int(data["original_question_num"])
    base["question"] = data["question"]
    base["options"] = data["options"]
    base["answer"] = str(data["answer"])
    if not base['question'] in questions:
      final_list.append(base)
      questions.add(base['question'])

In [ ]:
base_model['file_name'] = 'Diagnoostestid.pdf'
for data in data_list:
  base = base_model.copy()
  base["original_question_num"] = int(data["original_question_num"])
  base["question"] = data["question"]
  base["options"] = data["options"]
  base["answer"] = str(data["answer"])
  if not base['question'] in questions:
    final_list.append(base)
    questions.add(base['question'])

In [ ]:
with (SAVE_PATH / 'estonian_language_exams.json').open('w') as file:
  json.dump(final_list, file)

In [ ]:
f1, f2, f3 = [], [], []
for i, data in enumerate(tqdm(data_list)):
  soup = BeautifulSoup(data['html_question'], 'html.parser')
  soupan = BeautifulSoup(data['html'], 'html.parser')
  question = get_base_question(soup)
  select_elems = soup(['select'])
  mqas = soup.find_all('input', {'name': 'multiple_choice_result'})
  if len(mqas) > 1:
    options, answer = get_opt_an_simple(mqas, soupan)
    f1.append((i, question_div, question, options, answer))
  elif len(select_elems) == 1:
    options, answer = get_opt_an_sel1(select_elems[0], soupan)
    f2.append((i, question, options, answer))
  elif len(select_elems) > 1:
    options, answers, sub_questions = get_opt_an_sel_many(soup, soupan)
    if len(answers) > 0:
      f3.append((i, question, options, answers, sub_questions))
  else:
    continue # return [], [], []

In [ ]:
f3

In [ ]:
t = []
e = []
p = []
p2 = []
n_imgs_strong = 0
for i, data in enumerate(tqdm(data_list)):
  soup = BeautifulSoup(data['html_question'], 'html.parser')
  soupan = BeautifulSoup(data['html'], 'html.parser')
  question_div = soup.find('div', {'class': 'ilc_question_Standard'})
  select_elems = question_div.find_all('select')
  if len(select_elems) > 1:
    
    question_div = soup.find('div', {'class': 'ilc_question_Standard'})
    select_elems = question_div.find_all('select')
    if len(soup(['img'])) > 0 or len(question_div(['strong'])) > 0:
      n_imgs_strong += 1
      continue
    t.append((i, question_div))
    parents = [elem.parent for elem in select_elems]
    select_elems = [elem.extract() for elem in select_elems]
    nums_subques = [extract_number_and_text(s.getText(strip=True)) for s in parents]
    if any(x is None for x in nums_subques):
      e.append((i, question_div))
      continue
    ans_div = soupan.find_all('div', {'class': 'ilc_question_Standard'})[1]
    ans_txt = [ele.getText(strip=True) for ele in ans_div.find_all('span', {'class': 'solutionbox'})]
    opts = [[elem.getText(strip=True) for elem in elems(['option']) if int(elem.attrs['value'])>=0] for elems in select_elems]
    anss = [1+ops.index(ans) for ans, ops in zip(ans_txt, opts, strict=True)]
    assert any(a>0 for a in anss)
    if has_repeated(nums_subques):
      nums_subques, opts2, opts_expl = sep_num_ABC_mult(parents[0].getText('\n', strip=True))
      p2.append((i, nums_subques, opts2, opts_expl))
      continue
    p.append((i, nums_subques, opts))
    
  # if or len(soup.find_all('input', {'type': 'text'})) > 0:
  #   continue

In [ ]:
n_imgs_strong, len(t), len(e), len(p), len(p2)

In [ ]:
list1 = [['A', 'B', 'C'], ['A', 'B', 'C']]
list2 = [['A', 'B', 'C'], ['A', 'B', 'C']]
list1 == list2

In [ ]:
p2

In [ ]:
p[0], p2[0]

In [ ]:
insts

In [ ]:
data = data_list[73]
soup = BeautifulSoup(data['html_question'], 'html.parser')
soupan = BeautifulSoup(data['html'], 'html.parser')
question_elems = soup.find_all('div', {'class': 'ilc_qtitle_Title'})
assert len(question_elems) == 1
question = question_elems[0].text.strip()
instruction_elems = soup.find_all('h3')
assert len(instruction_elems) == 1
instruction = instruction_elems[0].text.strip()
middle_context = [extract_text_with_linebreaks(elem) for elem in get_elements_between(instruction_elems[0], soup.find('div', {'class': 'ilc_question_Standard'}))]
select_elems = soup.find_all('select')
mqas = soup.find_all('input', {'name': 'multiple_choice_result'})

In [ ]:
for i, data in enumerate(tqdm(data_list)):
  soup = BeautifulSoup(data['html_question'], 'html.parser')
  soupan = BeautifulSoup(data['html'], 'html.parser')
  select_elems = soup.find_all('select')
  if len(select_elems) > 1:
    assert len(soup.find_all('div', {'class': 'ilc_qanswer_Answer'}))==1

In [ ]:
soup

In [ ]:
[sou for sou in soup.find('div', {'class': 'ilc_qanswer_Answer'}).find_all('p') if sou.text.strip()]

In [ ]:
select_elems

In [ ]:
soup.find_all('input', {'name': 'multiple_choice_result'})[0]

In [ ]:
test

In [ ]:
img

In [ ]:
ilc_question_SingleChoice
ilc_qanswer_Answer

In [ ]:
soupan

In [ ]:
a = get_elements_between(instruction_elems[0], soup.find('div', {'class': 'ilc_question_Standard'}))[0]
print(get_text(a))

In [ ]:
print('\n\n'.join(middle_context))

In [ ]:
get_elements_between(instruction_elems[0], soup.find('div', {'class': 'ilc_question_Standard'}))

In [ ]:

from itertools import zip_longest

In [ ]:
def print_table_column_wise(html_content):
    # Parse the HTML content
    soup = BeautifulSoup(html_content, 'html.parser')
    
    # Find the table
    table = soup.find('table')
    
    if not table:
        print("No table found in the HTML content.")
        return
    
    # Extract headers
    headers = [th.text.strip() for th in table.find_all('th')]
    
    # Extract rows
    rows = []
    for tr in table.find_all('tr')[1:]:  # Skip the header row
        rows.append([td.text.strip() for td in tr.find_all('td')])
    
    # Transpose the data (swap rows and columns)
    columns = list(zip_longest(*rows, fillvalue=''))
    
    # Print column-wise
    for header, column in zip(headers, columns):
        print(f"{header}:")
        for item in column:
            print(f"  {item}")
        print()  # Empty line between columns

# Example usage
html_content = """
<table>
  <tr>
    <th>Name</th>
    <th>Age</th>
    <th>City</th>
  </tr>
  <tr>
    <td>John</td>
    <td>30</td>
    <td>New York</td>
  </tr>
  <tr>
    <td>Alice</td>
    <td>25</td>
    <td>Los Angeles</td>
  </tr>
  <tr>
    <td>Bob</td>
    <td>35</td>
    <td>Chicago</td>
  </tr>
</table>
"""

print_table_column_wise(html_content)


In [ ]:
def extract_text_with_linebreaks(element):
    texts = []
    for elem in element.descendants:
        if isinstance(elem, Comment):
            continue  # Skip comments
        if isinstance(elem, NavigableString):
            text = elem.strip()
            if text:
                texts.append(text)
        elif isinstance(elem, Tag):
            if elem.name == 'br':
                texts.append('\n')
            elif elem.name in ['p', 'div', 'tr']:
                if texts and not texts[-1].endswith('\n'):
                    texts.append('\n')
    return re.sub(r'\s*\n\s*', '\n', ' '.join(texts)).strip()
  


def process_table(table):
    rows = table.find_all('tr')
    if len(rows) <= 2:
        data = defaultdict(list)
        headers = []
        
        for i, row in enumerate(rows):
            cells = row.find_all(['th', 'td'])
            for j, cell in enumerate(cells):
                if i == 0:
                    headers.append(cell.get_text(strip=True))
                else:
                    data[headers[j]].append(cell.get_text(strip=True))
        
        # Print column-wise
        for header, values in data.items():
            print(f"{header}: {', '.join(values)}")
    else:
        print(f"Table has more than 2 rows ({len(rows)} rows). Not printing.")

In [ ]:
soup.find_all('h3')[0].text.strip()

In [ ]:
soup.find_all('h3')[0].parent

In [ ]:
print(extract_text_with_linebreaks(soup.find_all('h3')[0].parent))

In [ ]:
soup.find_all('div', {'class': 'ilc_qtitle_Title'})[0].text.strip()

In [ ]:
soup.find('div', {'class': 'ilc_question_Standard'})

In [ ]:
extract_numbers_except_first(data_list[0]['title_inner'])

In [ ]:


# Test cases
test_cases = [
    'Lugemistesti 1. ülesanne, 3. küsimus',
    'Lugemistesti 1. ülesanne, 4. küsimus',
    'Lugemistesti 2. ülesanne, 6.-10. küsimus',
    'This is a test 1. with multiple 2. numbers 3. in it.'
]

for case in test_cases:
    result = extract_numbers(case)
    print(f"Input: {case}")
    print(f"Extracted: {result}")
    print(get_num_from_title(case))
    print()

In [ ]:
page = driver.find_element(By.ID, 'ilc_Page').get_attribute('innerHTML')
page_name = driver.find_element(By.CLASS_NAME, 'ilc_page_title_PageTitle').text.strip()
scraped_data[super_name][test_name2][page_name] = {'page': page}

In [ ]:
take_full_div_screenshot(driver, 'ilc_Page')

In [ ]:
driver.get_window_size()

In [ ]:
link = driver.find_element(By.PARTIAL_LINK_TEXT, 'Järgmine')
link.click()

In [ ]:
try:
  link = driver.find_element(By.PARTIAL_LINK_TEXT, 'Järgmine')
  link.click()
except NoSuchElementException:
  end_test_questions = True

link = driver.find_element(By.PARTIAL_LINK_TEXT, 'Lõpeta test')
link.click()
link = driver.find_element(By.PARTIAL_LINK_TEXT, 'Vaata vastuseid')
link.click()
test_link_corrections = driver.current_url

In [ ]:
links, names, ids = get_test_table(driver)

In [ ]:
driver.get(links[0])

In [ ]:
png = driver.get_screenshot_as_png()

# Convert to JPG
im = Image.open(BytesIO(png))
im = im.convert('RGB')

In [ ]:
driver.set_window_size(1366, 2000)

In [ ]:
Image.open(BytesIO(driver.find_element(By.ID, 'ilc_Page').screenshot_as_png))

In [ ]:
driver.find_element(By.ID, 'ilTopBar').

In [ ]:
div = driver.find_element(By.ID, 'ilc_Page')

# Get the div's size
div_height = driver.execute_script("return arguments[0].offsetHeight;", div)
div_width = driver.execute_script("return arguments[0].offsetWidth;", div)

In [ ]:
div_width

In [ ]:
'fixed_content'

In [ ]:
take_full_div_screenshot(driver, 'ilc_Page')

In [ ]:
question_name = driver.find_element(By.CLASS_NAME, 'ilc_page_title_PageTitle').text
instruction = driver.find_element(By.CLASS_NAME, 'ilc_heading3_Headline3').text
question = driver.find_element(By.CLASS_NAME, 'ilc_qtitle_Title').text
table = driver.find_elements(By.CLASS_NAME, 'ilc_table_StandardTable')[-1]
answers = driver.find_element(By.CLASS_NAME, 'ilc_qinput_ClozeGapSelect')
answers_options = [elem.text for elem in answers.find_elements(By.TAG_NAME, 'option') if int(elem.get_attribute('value'))>=0]
scraped_data[test_name2][question_name] = {
  "category_original_lang": test_name2,
  "original_question_num": int(question_name.split(',')[-1].split('.')[0].strip()),
  "question": instruction +'\n\n'+ table_to_text(driver, table) + '\n\n'+question,
  "options": answers_options
}
scraped_data[test_name2][question_name]

In [ ]:
question_name = driver.find_element(By.CLASS_NAME, 'ilc_page_title_PageTitle').text
instruction = driver.find_element(By.CLASS_NAME, 'ilc_heading3_Headline3').text
question = driver.find_element(By.CLASS_NAME, 'ilc_qtitle_Title').text
text = driver.find_element(By.CSS_SELECTOR, '.ilc_Paragraph.ilc_text_block_List').text.strip()
example = driver.find_element(By.CSS_SELECTOR, '.ilc_Paragraph.ilc_heading2_Headline2').text.strip()
garbled_questions = driver.find_element(By.CSS_SELECTOR, '.ilc_qanswer_Answer.ilc_answers.answers.ilAssClozeTest.ilClearFloat')
paragraphs = [elem for elem in garbled_questions.find_elements(By.TAG_NAME, 'p') if elem.text.strip()]
q_especifics = [par.text.split('.')[1].split('\n')[0].strip() for par in paragraphs]
q_nums = [int(par.text.split('.')[0].strip()) for par in paragraphs]
q_options = [[elem.text for elem in par.find_elements(By.TAG_NAME, 'option') if int(elem.get_attribute('value'))>=0] for par in paragraphs]
scraped_data[test_name2][question_name] = [{
  "category_original_lang": test_name2,
  "original_question_num": q_num,
  "question": instruction +'\n\n'+ text + '\n\n' + example + '\n\n' +question + '\n\n' + q_esp,
  "options": an_opt
} for q_num, q_esp, an_opt in zip(q_nums, q_especifics, q_options)]
scraped_data[test_name2][question_name]

In [ ]:
print(scraped_data[test_name2][question_name]['question'])

In [ ]:
link = driver.find_element(By.PARTIAL_LINK_TEXT, 'Järgmine')
link.click()

In [ ]:
answers.find_elements(By.TAG_NAME, 'option')[0].get_attribute('value')

In [ ]:
scraped_data[test_name2] = {}

In [ ]:
answers_options

In [ ]:
print()

In [ ]:
def table_to_text(driver, table):
    # Find all rows in the table
    rows = table.find_elements(By.TAG_NAME, "tr")
    
    # Determine the number of columns
    first_row = rows[0]
    num_columns = len(first_row.find_elements(By.XPATH, "./td|./th"))
    
    # Initialize a list to store each column's text
    columns_text = ["" for _ in range(num_columns)]
    
    # Iterate through each row
    for row in rows:
        cells = row.find_elements(By.XPATH, "./td|./th")
        
        # Add each cell's text to the corresponding column's text
        for i, cell in enumerate(cells):
            columns_text[i] += cell.text.strip().replace('\n', ' ') + '   '
    
    # Join all columns with a separator
    return "\n".join(column.strip() for column in columns_text)


In [ ]:
print(table_to_text(driver, table))

In [ ]:
instruction.text

In [ ]:
    
    questions_answers = driver.find_elements(By.CLASS_NAME, 'ilc_question_SingleChoice')
    question = questions_answers[0].find_element(By.CLASS_NAME, 'ilc_qtitle_Title')
    answers = questions_answers[1].find_elements(By.CLASS_NAME, 'ilc_qanswer_Answer')
    answers_options = [elem.text for elem in answers]
    correct = [i+1 for i, elem in enumerate(answers) if elem.find_element(By.TAG_NAME, 'img').get_attribute('alt')=='Kontrollitud']
    assert instruction.text
    assert question.text
    assert len(correct) == 1
    scraped_data[test_name][question_id] = {
      "category_original_lang": test_name,
      "original_question_num": question_id,
      "question": instruction.text + '\n' + question.text,
      "options": answers_options,
      "answer": str(correct[0])
    }

In [ ]:
link = driver.find_element(By.PARTIAL_LINK_TEXT, 'Lõpeta test')
link.click()

link = driver.find_element(By.PARTIAL_LINK_TEXT, 'Vaata vastuseid')
link.click()
test_link_corrections = driver.current_url

In [ ]:
table = driver.find_element(By.CLASS_NAME, 'table-striped').find_element(By.TAG_NAME, 'tbody')
questions = table.find_elements(By.TAG_NAME, 'a')
questions_links = [elem.get_attribute('href') for elem in questions]
questions_names = [elem.text for elem in questions]
questions_ids = [int(elem.find_elements(By.TAG_NAME, 'td')[1].text) for elem in table.find_elements(By.TAG_NAME, 'tr')]

In [ ]:
questions_names

In [ ]:
driver.quit()

In [ ]:
'Eesti keele tasemeeksamid'

In [ ]:
!pip install PyPDF2